# PROC SQL Partie_2

## Segmentation dans une variable

Avec `proc SQL`, il est très facile de créer des catégories dans une table. Contrairement au _data step_, nous ne sommes plus obligés de conditionneur avec des `if`. Il suffit d'inclure toutes les conditions dans la clause `case`.

* Dans l'exemple suivant, nous allons diviser nos assurés en trois groupes d'âge;
    1. age $<$ 40 : EncoreJeune
    2. age $\leq$40 $<$ 60 : Pas Vieux
    3. age $>$ 40  : Commence Vieux

* Nous allons aussi afficher seulement la somme des coûts de sinistre
* Finalement, pour montrer qu'on peut ajouter une variable qui est basée sur une variable nouvellement calculée dans la même requête, nous allons calculer le coût de sinistre avec un supplément de 2% sur 5 ans (une sorte d'inflation comme exemple) 

In [3]:
libname libSql "data";
proc sql outobs=5;
    title 'Créer des catégories';
    select numeropol,
        langue,
        type_prof,
        type_territoire, 
        sum(cout1, cout2, cout3,cout4,cout5,cout6,cout7)as coutTotal format=dollar15.2, 
        calculated CoutTotal*(1.02**5) as coutTotalInfla format=dollar15.2, 
        2005 - year(date_naissance) as age,
            case 
                when calculated age < 40 then 'EncoreJeune'
                when calculated age ge 40 and calculated age < 60 then 'Pas Vieux'
                when calculated age ge 60 then 'Commence Vieux'
            end as categorieAge
        from libSql.equipe_1
quit; 

# Triage des données

Avec la procédure `PROC SQL`, le triage de données se fait facilement avec `ORDER BY`

### Trier par une colonne

In [4]:
proc sql outobs=5;
    title 'données triées par le nombre de sinistre';
    select numeropol,alimentation ,nbsin
        from libSql.equipe_1
        order by nbsin;
quit; 

### Trier par de multiples colonnes

In [5]:
proc sql outobs=5;
   title 'données triées par nombre de sinistre et alimentation';
    select numeropol,alimentation ,nbsin
        from libSql.equipe_1
        order by nbsin,alimentation;
quit; 

### Triage en ordre croissant ou décroissant

In [6]:
proc sql outobs=5;
    title 'Table génerale contenant toutes les informations';
    select numeropol,alimentation ,nbsin
        from libSql.equipe_1
        order by nbsin  desc,alimentation;
quit; 

L'ordre peut être dans n'importe quel ordre

In [25]:
proc sql outobs=5;
    select numeropol,alimentation ,nbsin
        from libSql.equipe_1
        order by nbsin  desc,numeropol asc;
quit; 
title;

### Trier sur des colonnes avec valeur calculée
On peut aussi trier sur des variables calculées! c'est formidable! réfléchissez bien lorsqu'on programmait jadis en `vba`. Calculons l'âge de nos assurés et faisons un tri sur cette variable calculée.

In [43]:
proc sql outobs=5;
    select numeropol,alimentation ,nbsin  ,      
        2005 - year(date_naissance) as age           
        from libSql.equipe_1
        order by nbsin desc, age asc;
quit; 

Au lieu de spécifier le nom de la colonne sur laquelle nous voulons appliquer un tri, nous pouvons le faire en indiquant le numéro de la colonne (position de la colonne)

In [26]:
proc sql outobs=5;
    title 'Créer des catégories';
    select numeropol,alimentation ,nbsin  ,      
        2005 - year(date_naissance) as age           
        from libSql.equipe_1
        order by 3 desc, 4 asc;
quit; 

### Trier sur des colonnes non sélectionnées

Il est aussi possible de faire un triage sur des colonnes non sélectionnées, par exemple ici, nous sélectionnons seulement `numeropol, alimentation ,nbsin  , age` mais nous appliquons un tri sur type_territoire. 

In [27]:
proc sql outobs=5;
    select numeropol,alimentation ,nbsin  ,      
        2005 - year(date_naissance) as age           
        from libSql.equipe_1
        order by type_territoire desc;
quit; 
title;

# La sélection d'observation

## Sélectionner des observations selon leurs valeurs

Le tableau suivant présente un sommaire des comparateurs logiques. ([Lien vers la documentation SAS](https://documentation.sas.com/?docsetId=lrcon&docsetTarget=p00iah2thp63bmn1lt20esag14lh.htm&docsetVersion=9.4&locale=en))

<table id="p0rf8k265ufy73n1w9uho24uglxc" class="xisDoc-table">
               <caption class="xisDoc-title">Comparison Operators</caption>
               <tbody><tr>
                  <th class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <p class="xisDoc-paragraph">Symbol</p>
                  </th>
                  <th class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <p class="xisDoc-paragraph">Mnemonic Equivalent</p>
                  </th>
                  <th class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <p class="xisDoc-paragraph">Definition</p>
                  </th>
                  <th class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <p class="xisDoc-paragraph">Example</p>
                  </th>
               </tr>
               <tr>
                  <td class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <p class="xisDoc-paragraph">=</p>
                  </td>
                  <td class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <p class="xisDoc-paragraph">EQ</p>
                  </td>
                  <td class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <p class="xisDoc-paragraph">equal to</p>
                  </td>
                  <td class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <pre class="xisDoc-codeFragment"><code>a=3</code></pre>
                  </td>
               </tr>
               <tr>
                  <td class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <p class="xisDoc-paragraph">^=</p>
                  </td>
                  <td class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <p class="xisDoc-paragraph">NE</p>
                  </td>
                  <td class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <p class="xisDoc-paragraph">not equal to<a class="xisDoc-legendRef" href="#n0abducv0013l7n1402h532sb7ql" ng-click="handleTopicLink($event)" ng-right-click="handleRightClickTopicLink($event)" tabindex="0">1</a></p>
                  </td>
                  <td class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <pre class="xisDoc-codeFragment"><code>a
ne 3</code></pre>
                  </td>
               </tr>
               <tr>
                  <td class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <p class="xisDoc-paragraph">¬=</p>
                  </td>
                  <td class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <p class="xisDoc-paragraph">NE</p>
                  </td>
                  <td class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <p class="xisDoc-paragraph">not equal to</p>
                  </td>
                  <td style="text-align: left">
                     <p class="xisDoc-paragraph"> </p>
                  </td>
               </tr>
               <tr>
                  <td class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <p class="xisDoc-paragraph">~=</p>
                  </td>
                  <td class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <p class="xisDoc-paragraph">NE</p>
                  </td>
                  <td class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <p class="xisDoc-paragraph">not equal to</p>
                  </td>
                  <td style="text-align: left">
                     <p class="xisDoc-paragraph"> </p>
                  </td>
               </tr>
               <tr>
                  <td class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <p class="xisDoc-paragraph">&gt;</p>
                  </td>
                  <td class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <p class="xisDoc-paragraph">GT</p>
                  </td>
                  <td class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <p class="xisDoc-paragraph">greater than</p>
                  </td>
                  <td class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <pre class="xisDoc-codeFragment"><code>num&gt;5</code></pre>
                  </td>
               </tr>
               <tr>
                  <td class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <p class="xisDoc-paragraph">&lt;</p>
                  </td>
                  <td class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <p class="xisDoc-paragraph">LT</p>
                  </td>
                  <td class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <p class="xisDoc-paragraph">less than</p>
                  </td>
                  <td class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <pre class="xisDoc-codeFragment"><code>num&lt;8</code></pre>
                  </td>
               </tr>
               <tr>
                  <td class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <p class="xisDoc-paragraph">&gt;=</p>
                  </td>
                  <td class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <p class="xisDoc-paragraph">GE</p>
                  </td>
                  <td class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <p class="xisDoc-paragraph">greater than or equal
                        to<a class="xisDoc-legendRef" href="#n129omc36zeyenn173bx6acx9o53" ng-click="handleTopicLink($event)" ng-right-click="handleRightClickTopicLink($event)" tabindex="0">2</a></p>
                  </td>
                  <td class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <pre class="xisDoc-codeFragment"><code>sales&gt;=300</code></pre>
                  </td>
               </tr>
               <tr>
                  <td class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <p class="xisDoc-paragraph">&lt;=</p>
                  </td>
                  <td class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <p class="xisDoc-paragraph">LE</p>
                  </td>
                  <td class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <p class="xisDoc-paragraph">less than or equal to<a class="xisDoc-legendRef" href="#p0elrtpasw8w6jn0zakv2bghnz4n" ng-click="handleTopicLink($event)" ng-right-click="handleRightClickTopicLink($event)" tabindex="0">3</a></p>
                  </td>
                  <td class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <pre class="xisDoc-codeFragment"><code>sales&lt;=100</code></pre>
                  </td>
               </tr>
               <tr>
                  <td style="text-align: left">
                     <p class="xisDoc-paragraph"> </p>
                  </td>
                  <td class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <p class="xisDoc-paragraph">IN</p>
                  </td>
                  <td class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <p class="xisDoc-paragraph">equal to one of a list</p>
                  </td>
                  <td class="xisDoc-horizontalLeft xisDoc-verticalTop">
                     <pre class="xisDoc-codeFragment"><code>num
in (3, 4, 5)</code></pre>
                  </td>
               </tr>
               <tr>
                  <td class="xisDoc-legend" colspan="4" id="n0abducv0013l7n1402h532sb7ql"><span class="xisDoc-legendRefSymbol">1</span> The symbol that you use
                     for NE depends on your personal computer.</td>
               </tr>
               <tr>
                  <td class="xisDoc-legend" colspan="4" id="n129omc36zeyenn173bx6acx9o53"><span class="xisDoc-legendRefSymbol">2</span> The symbol =&gt; is also
                     accepted for compatibility with previous releases of SAS. It is not
                     supported in WHERE clauses or in PROC SQL.</td>
               </tr>
               <tr>
                  <td class="xisDoc-legend" colspan="4" id="p0elrtpasw8w6jn0zakv2bghnz4n"><span class="xisDoc-legendRefSymbol">3</span> The symbol =&lt; is also
                     accepted for compatibility with previous releases of SAS. It is not
                     supported in WHERE clauses or in PROC SQL.</td>
               </tr>
            </tbody></table>

Par exemple, sélectionnons les assurés ayant plus que 3 sinistres

In [28]:
proc sql outobs=5;
    title 'Créer des catégories';
    select numeropol,alimentation ,nbsin  ,      
        2005 - year(date_naissance) as age           
        from libSql.equipe_1
        where nbsin gt 3
        order by 1 desc;
quit; 

## Sélection des observations selon plusieurs conditions

Sélectionnons des assurés âgés de moins de 40 ans et ayant plus trois sinistres. N'oublions pas que la colonne `age` est une variable calculée!

In [29]:
proc sql outobs=5;
    title 'Créer des catégories';
    select numeropol,alimentation ,nbsin  ,      
        2005 - year(date_naissance) as age           
        from libSql.equipe_1
        where nbsin gt 3 and calculated age lt 40
        order by 1 desc;
quit; 

## D'autres opérateurs conditionnels

Avec l'opérateur l'opération `WHERE`, nous pouvons utiliser plusieurs opérateurs;

ANY

specifies that at least one of a set of values obtained from a subquery must satisfy a given condition

`where Population> any (select Population from sql.countries)`

ALL

specifies that all of the values obtained from a subquery must satisfy a given condition

`where Population > all (select Population from sql.countries)`

BETWEEN-AND

tests for values within an inclusive range

`where Population between 1000000 and 5000000`

CONTAINS

tests for values that contain a specified string

`where Continent contains 'America';`

EXISTS

tests for the existence of a set of values obtained from a subquery

`where exists (select * from sql.oilprod);`

IN

tests for values that match one of a list of values

`where Name in ('Africa', 'Asia');`

IS NULL or IS MISSING

tests for missing values

`where Population is missing;`

LIKE

tests for values that match a specified pattern ([footnote 1](#p114vm628bnawan1av42nioe1ule-note1))

`where Continent like 'A%';`

\=\*

tests for values that sound like a specified value

`where Name=* 'Tiland';`

### Exemple d'opérateur `IN`

In [31]:
proc sql outobs=5;
    title "titre";
    select 
        numeropol, 
        langue,
        type_prof,
        alimentation
        from libSql.equipe_1
        where type_prof in ('Informaticien','Technicien')
        order by numeropol;
quit; 

### Exemple d'opérateur `LIKE`

In [32]:
proc sql outobs=5;
    title "titre";
    select 
        numeropol, 
        langue,
        type_prof,
        alimentation
        from libSql.equipe_1
        where type_prof like "%cien"
        order by numeropol;
quit; 

## Sommaire des données

Il est possible d'appliquer plusieurs fonctions [_aggregate_](https://go.documentation.sas.com/doc/en/pgmsascdc/9.4_3.5/sqlproc/p0xwc73ekemkapn1byhceqrwrisb.htm#:~:text=The%20aggregate%20function%20instructs%20PROC,that%20are%20listed%20are%20calculated.) sur des colonnes, comme des moyennes, des MIN/Max...etc. La liste complète est dans le tableau ci-dessous.

| Function | Definition |
| :--- | :--- |
| AVG, MEAN | mean or average of values |
| COUNT, FREQ, N | number of nonmissing values |
| CSS | corrected sum of squares |
| CV | coefficient of variation (percent) |
| MAX | largest value |
| MIN | smallest value |
| NMISS | number of missing values |
| PRT | probability of a greater absolute value of Student's t |
| RANGE | range of values |
| STD | standard deviation |
| STDERR | standard error of the mean |
| SUM | sum of values |
| SUMWGT | sum of the WEIGHT variable values (footnote 1) |
| VAR | variance |

**Exemple**: Nous voudrions avoir un tableau avec contenant le numeropol, debut_pol, fin_pol et **la moyenne des coûts de sinistres 1 à 7**. Toutefois, nous voulons seulement les moyennes supérieures à 1000$

In [7]:
proc sql outobs=5;
    title "Coûts moyens des sinistres";
    select 
        numeropol, 
        debut_pol, 
        fin_pol, 
        mean(cout1, cout2, cout3,cout4,cout5,cout6,cout7) as coutMoyen format=dollar15.2
        from libSql.equipe_1
        where calculated coutMoyen gt 1000;
quit;